# Example

In [1]:
import os
import sys
import torch
import numpy as np
import soundfile as sf
from IPython.display import Audio

sys.path.append(
    os.path.abspath(
        os.path.join(
            os.path.dirname(os.path.realpath("file")), os.pardir, os.pardir, "ChatTTS"
        )
    )
)
import ChatTTS

torch._dynamo.config.cache_size_limit = 64  # type: ignore
torch._dynamo.config.suppress_errors = True  # type: ignore
torch.set_float32_matmul_precision("high")

## Load Models

In [2]:
chat = ChatTTS.Chat()
chat.load_models(source="local", local_path="chattts/resources/nosft")

INFO:ChatTTS.core:Load from local: chattts/resources/nosft
INFO:ChatTTS.core:use cuda:0
INFO:ChatTTS.core:vocos loaded.
INFO:ChatTTS.core:dvae loaded.
INFO:ChatTTS.core:gpt loaded.
INFO:ChatTTS.core:decoder loaded.
INFO:ChatTTS.core:tokenizer loaded.
INFO:ChatTTS.core:All initialized.


## Inference

### Batch infer

In [4]:
texts = [
    "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",
] + [
    "我觉得像我们这些写程序的人，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，他们并不会轻易的开放给所有的人用。"
]

wavs = chat.infer(texts)

INFO:ChatTTS.core:All initialized.
 NeMo-text-processing :: INFO     :: Creating ClassifyFst grammars.
INFO:NeMo-text-processing:Creating ClassifyFst grammars.
2024-06-13 22:57:59,264 WETEXT INFO found existing fst: /home/wanghao/code/Python/FunnyProject/.venv_audio/lib/python3.10/site-packages/tn/zh_tn_tagger.fst
INFO:wetext-zh_normalizer:found existing fst: /home/wanghao/code/Python/FunnyProject/.venv_audio/lib/python3.10/site-packages/tn/zh_tn_tagger.fst
2024-06-13 22:57:59,265 WETEXT INFO                     /home/wanghao/code/Python/FunnyProject/.venv_audio/lib/python3.10/site-packages/tn/zh_tn_verbalizer.fst
INFO:wetext-zh_normalizer:                    /home/wanghao/code/Python/FunnyProject/.venv_audio/lib/python3.10/site-packages/tn/zh_tn_verbalizer.fst
2024-06-13 22:57:59,266 WETEXT INFO skip building fst for zh_normalizer ...
INFO:wetext-zh_normalizer:skip building fst for zh_normalizer ...
 43%|████▎     | 872/2048 [00:08<00:11, 99.90it/s] 


In [5]:
Audio(data=wavs[0], rate=24_000, autoplay=True)

In [6]:
Audio(data=wavs[1], rate=24_000, autoplay=True)

### Custom params
params_refine_text

句子级控制
 - oral_(0-9) 口腔特征
 - laugh_(0-2) 笑声特征
 - break_(0-7) 停顿特征

单词级控制
 - laugh 笑声
 - uv_break 停顿

params_infer_code
 - speed_5 语言速度
 - spk_emb 说话者身份
 - temperature、top_P、top_K 解码策略

In [10]:
text = "四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片等，每样都让人垂涎三尺。"
params_refine_text = {"prompt": "[oral_2][laugh_0][break_6]"}
params_infer_code = {"prompt": "[speed_5]", "temperature": 0.3}

wavs = chat.infer(
    text=text,
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)

INFO:ChatTTS.core:All initialized.
 19%|█▉        | 393/2048 [00:03<00:13, 121.97it/s]


In [11]:
Audio(data=wavs[0], rate=24_000, autoplay=True)

### fix random speaker

In [12]:
text = "四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃的口味温和，甜而不腻，也很受欢迎。"
params_refine_text = {"prompt": "[oral_5][laugh_1][break_3]"}
params_infer_code = {
    "spk_emb": chat.sample_random_speaker(),
    "temperature": 0.3,
    "top_P": 0.7,
    "top_K": 20,
}

wavs = chat.infer(
    text=text,
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)

INFO:ChatTTS.core:All initialized.
 25%|██▍       | 511/2048 [00:19<00:59, 25.85it/s] 


In [13]:
Audio(data=wavs[0], rate=24_000, autoplay=True)

### Two stage control

In [16]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
text = chat.infer(text, refine_text_only=True)
wavs = chat.infer(text, skip_refine_text=True)

INFO:ChatTTS.core:All initialized.
 22%|██▏       | 84/384 [00:00<00:03, 98.16it/s] 
INFO:ChatTTS.core:All initialized.
 40%|████      | 822/2048 [00:07<00:10, 113.20it/s]


In [17]:
display(text)
Audio(data=wavs[0], rate=24_000, autoplay=True)

['so we found being competitive and collaborative [uv_break] was a huge way [uv_break] of staying motivated towards our goals, [uv_break] so [uv_break] one person to call when you fall off, one person who gets you back [uv_break] on [uv_break] then one person to actually do the activity [uv_break] with.']

## Summary

In [24]:
text = "鸡哥，人家真的很想骂你，真的可恶呀。"
text = chat.infer(text, refine_text_only=True)
display(text)

spk_emb = torch.as_tensor(
    data=np.load("datas/women_speaker_latent.npy"), dtype=torch.float32, device="cuda:0"
)
params_refine_text = {"prompt": "[oral_2][laugh_0][break_3]"}
params_infer_code = {
    "prompt": "[speed_5]",
    "spk_emb": spk_emb,
    "temperature": 0.3,
    "top_P": 0.7,
    "top_K": 20,
}
wavs = chat.infer(
    text,
    skip_refine_text=True,
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)
sf.write(file="results/example.wav", data=wavs[0].T, samplerate=24_000)
Audio(data=wavs[0], rate=24_000, autoplay=True)

INFO:ChatTTS.core:All initialized.
  5%|▌         | 21/384 [00:00<00:07, 46.83it/s]


['鸡 哥 ， 人 家 真 的 很 想 骂 你 ， 真 的 可 恶 呀 。']

INFO:ChatTTS.core:All initialized.
  7%|▋         | 140/2048 [00:01<00:15, 122.33it/s]
